In [6]:
from ray.tune.schedulers import ASHAScheduler
import random

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import ray
import torch
from ray import tune
from torch.utils.data import DataLoader
from torchvision import datasets
from torchvision.transforms import transforms
from tqdm import tqdm
from ray.tune.suggest.bayesopt import BayesOptSearch

from gene.optimisers.annealed_crossing import AnnealedCrossingOptimiser
from gene.targets import get_negative_accuracy_target
from gene.util import get_accuracy

random.seed(0)
torch.manual_seed(0)
np.random.seed(0)

DEVICE = ["cpu", "cuda"][0]
N_EPOCHS = 5

train_data = datasets.MNIST(
    root="./cache",
    download=True,
    train=True,
    transform=transforms.ToTensor()
)
test_data = datasets.MNIST(
    root="./cache",
    download=True,
    train=False,
    transform=transforms.ToTensor()
)
train_data = ray.put(train_data)
test_data = ray.put(test_data)


def train(config):
    # Define the model
    model = torch.nn.Sequential(
        torch.nn.Flatten(),
        torch.nn.Linear(28 * 28, 256),
        torch.nn.ReLU(),
        torch.nn.Linear(256, 64),
        torch.nn.ReLU(),
        torch.nn.Linear(64, 10)
    )
    models = [model.to(DEVICE)]

    # Define the optimiser
    optimiser = AnnealedCrossingOptimiser(target_func=get_negative_accuracy_target,
                                          init_std=config["init_std"],
                                          std_updater=lambda std: std * config["decay"] if std >= 0.0001 else std,
                                          max_couples=10,
                                          n_children_per_couple=2,
                                          selection_limit=10,
                                          device=DEVICE)

    # Define the data loaders
    train_loader = DataLoader(ray.get(train_data), batch_size=1024, shuffle=True)
    test_loader = DataLoader(ray.get(test_data), batch_size=1024)

    for e in range(N_EPOCHS):
        for images, labels in train_loader:
            models = optimiser.step(models, images.to(DEVICE), labels.to(DEVICE))

        tune.report(np.mean([get_accuracy(test_loader, m, DEVICE) for m in models]))


parameters = {"decay": tune.uniform(0, 1.0),
              "init_std": tune.uniform(0.01, 20)}
search_alg = BayesOptSearch(metric="_metric", mode="max")
analysis = tune.run(
    train,
    search_alg=search_alg,
    scheduler=ASHAScheduler(metric="_metric", mode="max"),
    config=parameters,
    time_budget_s=3600,
    num_samples=-1,
#     resources_per_trial={'gpu': 1},
)

2022-06-22 16:44:15,149	WARNING bayesopt.py:397 -- BayesOpt does not support specific sampling methods. The Uniform sampler will be dropped.
2022-06-22 16:44:15,150	WARNING bayesopt.py:397 -- BayesOpt does not support specific sampling methods. The Uniform sampler will be dropped.
2022-06-22 16:44:15,152	WARNING tune.py:574 -- Tune detects GPUs, but no trials are using GPUs. To enable trials to use GPUs, set tune.run(resources_per_trial={'gpu': 1}...) which allows Tune to expose 1 GPU to each trial. You can also override `Trainable.default_resource_request` if using the Trainable API.


Result for train_c9a1d52c:
  _metric: 0.19280000000000003
  date: 2022-06-22_16-44-48
  done: false
  experiment_id: f3122bddeac040679f8ee724f2b25b32
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 1
  node_ip: 217.105.36.71
  pid: 7579
  time_since_restore: 31.480254650115967
  time_this_iter_s: 31.480254650115967
  time_total_s: 31.480254650115967
  timestamp: 1655909088
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: c9a1d52c
  
Result for train_ca497264:
  _metric: 0.1878
  date: 2022-06-22_16-44-48
  done: true
  experiment_id: d676b1bb8426416bb0ab3d263f8876ff
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 1
  node_ip: 217.105.36.71
  pid: 7629
  time_since_restore: 31.290218353271484
  time_this_iter_s: 31.290218353271484
  time_total_s: 31.290218353271484
  timestamp: 1655909088
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: ca497264
  
Result for train_ca071edc:
  _metric: 0.15421
  date: 2022-06-22_16-

Result for train_c9a1d52c:
  _metric: 0.19280000000000003
  date: 2022-06-22_16-45-13
  done: false
  experiment_id: f3122bddeac040679f8ee724f2b25b32
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 2
  node_ip: 217.105.36.71
  pid: 7579
  time_since_restore: 56.77218461036682
  time_this_iter_s: 25.291929960250854
  time_total_s: 56.77218461036682
  timestamp: 1655909113
  timesteps_since_restore: 0
  training_iteration: 2
  trial_id: c9a1d52c
  
Result for train_c9f14b3e:
  _metric: 0.2298
  date: 2022-06-22_16-45-14
  done: false
  experiment_id: 7f0211a19e064f14af7598c40bbf5713
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 2
  node_ip: 217.105.36.71
  pid: 7580
  time_since_restore: 57.913819789886475
  time_this_iter_s: 25.386528491973877
  time_total_s: 57.913819789886475
  timestamp: 1655909114
  timesteps_since_restore: 0
  training_iteration: 2
  trial_id: c9f14b3e
  
Result for train_cb0a21bc:
  _metric: 0.1718
  date: 2022-06-22_16-45

Result for train_c9a1d52c:
  _metric: 0.19280000000000003
  date: 2022-06-22_16-45-36
  done: false
  experiment_id: f3122bddeac040679f8ee724f2b25b32
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 3
  node_ip: 217.105.36.71
  pid: 7579
  time_since_restore: 79.90580344200134
  time_this_iter_s: 23.13361883163452
  time_total_s: 79.90580344200134
  timestamp: 1655909136
  timesteps_since_restore: 0
  training_iteration: 3
  trial_id: c9a1d52c
  


Result for train_c9f14b3e:
  _metric: 0.2298
  date: 2022-06-22_16-45-38
  done: false
  experiment_id: 7f0211a19e064f14af7598c40bbf5713
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 3
  node_ip: 217.105.36.71
  pid: 7580
  time_since_restore: 81.42487335205078
  time_this_iter_s: 23.511053562164307
  time_total_s: 81.42487335205078
  timestamp: 1655909138
  timesteps_since_restore: 0
  training_iteration: 3
  trial_id: c9f14b3e
  
Result for train_dd9e0122:
  _metric: 0.22004
  date: 2022-06-22_16-45-38
  done: false
  experiment_id: cb09e1a997e04c07bdefab6ed49f6376
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 2
  node_ip: 217.105.36.71
  pid: 7804
  time_since_restore: 48.133456230163574
  time_this_iter_s: 23.14166569709778
  time_total_s: 48.133456230163574
  timestamp: 1655909138
  timesteps_since_restore: 0
  training_iteration: 2
  trial_id: dd9e0122
  
Result for train_cab38b9a:
  _metric: 0.3119
  date: 2022-06-22_16-45-39
  done: f

...

(scheduler +1h17m6s) Warning: The following resource request cannot be scheduled right now: {'CPU': 1.0}. This is likely due to all cluster resources being claimed by actors. Consider creating fewer actors or adding more nodes to this Ray cluster.
Result for train_d24069d4:
  _metric: 0.43264
  date: 2022-06-22_17-44-03
  done: true
  experiment_id: a268162098d14980a9aa23061959d40b
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 4
  node_ip: 217.105.36.71
  pid: 16906
  time_since_restore: 133.90194439888
  time_this_iter_s: 34.87322497367859
  time_total_s: 133.90194439888
  timestamp: 1655912643
  timesteps_since_restore: 0
  training_iteration: 4
  trial_id: d24069d4
  


Result for train_d35ef146:
  _metric: 0.48317000000000004
  date: 2022-06-22_17-44-09
  done: false
  experiment_id: 5dd87b7e6268435f924dde68dde66976
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 3
  node_ip: 217.105.36.71
  pid: 16944
  time_since_restore: 100.1605818271637
  time_this_iter_s: 33.95137071609497
  time_total_s: 100.1605818271637
  timestamp: 1655912649
  timesteps_since_restore: 0
  training_iteration: 3
  trial_id: d35ef146
  


Result for train_ea901700:
  _metric: 0.35790999999999995
  date: 2022-06-22_17-44-11
  done: false
  experiment_id: 8696820fdc674abf99fa3df716cff300
  hostname: yaroslav-B365-M-AORUS-ELITE
  iterations_since_restore: 3
  node_ip: 217.105.36.71
  pid: 16968
  time_since_restore: 97.80913496017456
  time_this_iter_s: 32.97304606437683
  time_total_s: 97.80913496017456
  timestamp: 1655912651
  timesteps_since_restore: 0
  training_iteration: 3
  trial_id: ea901700
  


2022-06-22 17:44:15,339	INFO stopper.py:344 -- Reached timeout of 3600 seconds. Stopping all trials.


2022-06-22 17:44:38,879	INFO tune.py:630 -- Total run time: 3623.73 seconds (3600.20 seconds for the tuning loop).


In [7]:
analysis_df = analysis.results_df
analysis_df

_metric  time_this_iter_s  done  timesteps_total  episodes_total  \
trial_id                                                                     
c9a1d52c  0.19280         23.163242  True              NaN             NaN   
c9f14b3e  0.22980         23.187739  True              NaN             NaN   
ca071edc  0.15421         32.011492  True              NaN             NaN   
ca497264  0.18780         31.290218  True              NaN             NaN   
ca5d5edc  0.19010         32.477345  True              NaN             NaN   
...           ...               ...   ...              ...             ...   
1a903e08      NaN               NaN   NaN              NaN             NaN   
1f7f25b4      NaN               NaN   NaN              NaN             NaN   
2160c1bc      NaN               NaN   NaN              NaN             NaN   
229759e2      NaN               NaN   NaN              NaN             NaN   
247844b0      NaN               NaN   NaN              NaN             NaN   

          training_iteration                     experiment_id  \
trial_id                                                         
c9a1d52c                 5.0  f3122bddeac040679f8ee724f2b25b32   
c9f14b3e                 5.0  7f0211a19e064f14af7598c40bbf5713   
ca071edc                 1.0  b0bda1d525f346ccb1b2256f4d183194   
ca497264                 1.0  d676b1bb8426416bb0ab3d263f8876ff   
ca5d5edc                 1.0  6fe857843925451da4284976af2b2e07   
...                      ...                               ...   
1a903e08                 NaN  576844a16aff4cfc82ba10807814910f   
1f7f25b4                 NaN  d4b306d9d3a641c5b0439cf9a7cf55f9   
2160c1bc                 NaN  6cf31e2471804199a713d0d26ed5c177   
229759e2                 NaN  a504fcfc9e5b45d683576c5a10a73139   
247844b0                 NaN                               NaN   

                         date     timestamp  time_total_s      pid  \
trial_id                                                             
c9a1d52c  2022-06-22_16-46-23  1.655909e+09    126.168668   7579.0   
c9f14b3e  2022-06-22_16-46-24  1.655909e+09    128.017720   7580.0   
ca071edc  2022-06-22_16-44-49  1.655909e+09     32.011492   7630.0   
ca497264  2022-06-22_16-44-48  1.655909e+09     31.290218   7629.0   
ca5d5edc  2022-06-22_16-44-50  1.655909e+09     32.477345   7676.0   
...                       ...           ...           ...      ...   
1a903e08  2022-06-22_17-43-58  1.655913e+09           NaN  17051.0   
1f7f25b4  2022-06-22_17-44-00  1.655913e+09           NaN  17078.0   
2160c1bc  2022-06-22_17-44-02  1.655913e+09           NaN  17103.0   
229759e2  2022-06-22_17-44-05  1.655913e+09           NaN  17128.0   
247844b0                  NaN           NaN           NaN      NaN   

                             hostname        node_ip  time_since_restore  \
trial_id                                                                   
c9a1d52c  yaroslav-B365-M-AORUS-ELITE  217.105.36.71          126.168668   
c9f14b3e  yaroslav-B365-M-AORUS-ELITE  217.105.36.71          128.017720   
ca071edc  yaroslav-B365-M-AORUS-ELITE  217.105.36.71           32.011492   
ca497264  yaroslav-B365-M-AORUS-ELITE  217.105.36.71           31.290218   
ca5d5edc  yaroslav-B365-M-AORUS-ELITE  217.105.36.71           32.477345   
...                               ...            ...                 ...   
1a903e08  yaroslav-B365-M-AORUS-ELITE  217.105.36.71                 NaN   
1f7f25b4  yaroslav-B365-M-AORUS-ELITE  217.105.36.71                 NaN   
2160c1bc  yaroslav-B365-M-AORUS-ELITE  217.105.36.71                 NaN   
229759e2  yaroslav-B365-M-AORUS-ELITE  217.105.36.71                 NaN   
247844b0                          NaN            NaN                 NaN   

          timesteps_since_restore  iterations_since_restore  \
trial_id                                                      
c9a1d52c                      0.0                       5.0   
c9f14b3e                      0.0              

In [9]:
analysis_df.to_csv("result.csv")

OSError: [Errno 107] Transport endpoint is not connected: '.'

In [8]:
import plotly.express as px


parameter_names = list(parameters.keys())
px.scatter(analysis_df, x=f"config.{parameter_names[0]}", y=f"config.{parameter_names[1]}", color="_metric")